In [1]:
import pandas as pd
from ast import literal_eval
import numpy as np
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))
from statistics import mean, median
import scipy
from sklearn.decomposition import PCA
from sklearn import preprocessing
from gprofiler import GProfiler
import warnings
warnings.filterwarnings('ignore')
import matplotlib.pyplot as plt
from matplotlib.pyplot import figure
figure(num=None, figsize=(8, 6), dpi=80, facecolor='w', edgecolor='k')
import operator
import qvalue as qv


#Reactome file containing information on pathways, the genes they contain and pathway name, also including the illumina identifier for the genes.

reactome = pd.read_csv('../data/reactome.csv', sep=',', index_col = 0)

def read_reactome(file_name, gene_name_start = "ENSG0"):
    df = pd.read_csv(file_name, sep='\t', header=None)
    
    if gene_name_start == None:
        sub_df = df
    else:
        subset_vec = df[0].str.startswith(gene_name_start)
        sub_df = df.loc[subset_vec]
    
    genes_df = sub_df.groupby(1)[0].apply(list)
    names_df = sub_df.groupby(1)[3].max()
    
    out_df = pd.concat([genes_df,names_df], axis=1)
    out_df.columns = ['genes', 'pathway_name']
    
    return out_df

low_level = read_reactome('../data/Ensembl2Reactome_All_Levels.txt.gz')

def my_pca(df, n_pc=1, normalize=True):
    df = df.dropna(axis = 0, how = 'all')#redundant, but keeping it just in case
    X = df.values.T
    if normalize:
        X2 = preprocessing.scale(X)
    else:
        X2 = X
    pca = PCA(n_components = n_pc)
    pca.fit(X2)
    my_pca.pca = pca  #needed for components
    Xnew = pca.fit_transform(X2)
    out_df = pd.DataFrame(Xnew.transpose(), index=list(range(1,n_pc+1)), columns=df.columns)
    out_df = out_df.transpose()
    
    return out_df, my_pca.pca.components_, my_pca.pca.explained_variance_ratio_

#Importing metabric dataset, dividing up what is clinical/expression data and changing the type of the expression columns to float
metabric_data = pd.read_csv('../data/metabric.csv.gz')
#clinical_data = metabric_data.iloc[:27, :]
expression_data = metabric_data.iloc[27:,:]

#print(expression_data.columns)
dtypedict = {}
for i in expression_data.columns[1:]:
    dtypedict[i] = 'float32'
expression_data = expression_data.astype(dtypedict)



new_clinical_patient = pd.read_csv('../data/data_clinical_patient.txt', sep='\t', index_col=0).iloc[4:]
new_clinical_sample = pd.read_csv('../data/data_clinical_sample.txt', sep='\t', index_col=0).iloc[4:]
new_clinical = pd.concat([new_clinical_patient, new_clinical_sample.reindex(new_clinical_patient.index)], axis=1)
new_clinical['Triple Neg'] = new_clinical.apply(lambda row: True if ((row['ER Status'] == 'Negative') 
                                                                     and (row['PR Status'] == 'Negative') 
                                                                     and (row['HER2 Status'] == 'Negative')) else False, axis = 1)

new_clinical['ER-/PR-/HER2+'] = new_clinical.apply(lambda row: True if ((row['ER Status'] == 'Negative') 
                                                                     and (row['PR Status'] == 'Negative') 
                                                                     and (row['HER2 Status'] == 'Positive')) else False, axis = 1)





genes = expression_data['Unnamed: 0'].values.tolist()

gp = GProfiler(return_dataframe = True)
gp = gp.convert(organism='hsapiens',
          query=genes)

gp = gp.loc[gp['n_converted'] == 1]
gp = gp.loc[gp['name'] != 'None']
gp = gp.set_index('incoming')
gprofiler_names = gp
gprofiler_names

dataset = expression_data.set_index('Unnamed: 0') #gene_patient
pca_per_pathway = pd.DataFrame(index=expression_data.columns)

real_gene_names = pd.read_csv('../data/illumina2symbol.txt', sep="\t", index_col = 0)



In [5]:
reactome


genes  \
1                                                                  
R-HSA-1059683  ['ENSG00000096968' 'ENSG00000105397' 'ENSG0000...   
R-HSA-109581   ['ENSG00000002330' 'ENSG00000003402' 'ENSG0000...   
R-HSA-109582   ['ENSG00000000938' 'ENSG00000002586' 'ENSG0000...   
R-HSA-109606   ['ENSG00000002330' 'ENSG00000015475' 'ENSG0000...   
R-HSA-109703               ['ENSG00000105221' 'ENSG00000152270']   
...                                                          ...   
R-HSA-983695   ['ENSG00000007312' 'ENSG00000010671' 'ENSG0000...   
R-HSA-983705   ['ENSG00000007312' 'ENSG00000008018' 'ENSG0000...   
R-HSA-983712   ['ENSG00000011021' 'ENSG00000016490' 'ENSG0000...   
R-HSA-991365   ['ENSG00000065135' 'ENSG00000078295' 'ENSG0000...   
R-HSA-997272   ['ENSG00000078369' 'ENSG00000111664' 'ENSG0000...   

                                                    pathway_name  \
1                                                                  
R-HSA-1059683                            Interleukin-6 signaling   
R-HSA-109581                                           Apoptosis   
R-HSA-109582                                          Hemostasis   
R-HSA-109606                     Intrinsic Pathway for Apoptosis   
R-HSA-109703                                 PKB-mediated events   
...                                                          ...   
R-HSA-983695   Antigen activates B Cell Receptor (BCR) leadin...   
R-HSA-983705              Signaling by the B Cell Receptor (BCR)   
R-HSA-983712                               Ion channel transport   
R-HSA-991365                       Activation of GABAB receptors   
R-HSA-997272   Inhibition  of voltage gated Ca2+ channels via...   

                                                        illumina  
1                                                                 
R-HSA-1059683  ['ILMN_1683178', 'ILMN_1676955', 'ILMN_2181968...  
R-HSA-109581   ['ILMN_1738652', 'ILMN_1789830', 'ILMN_1789176...  
R-HSA-109582   ['ILMN_2368318', 'ILMN_2056032', 'ILMN_1662619...  
R-HSA-109606   ['ILMN_1738652', 'ILMN_2259495', 'ILMN_1805990...  
R-HSA-109703                    ['ILMN_1743347', 'ILMN_2131381']  
...                                                          ...  
R-HSA-983695   ['ILMN_2366212', 'ILMN_1662026', 'ILMN_1781207...  
R-HSA-983705   ['ILMN_2366212', 'ILMN_1789176', 'ILMN_1662026...  
R-HSA-983712   ['ILMN_1741594', 'ILMN_1797219', 'NaN', 'ILMN_...  
R-HSA-991365   ['ILMN_1696003', 'ILMN_1810691', 'ILMN_1760320...  
R-HSA-997272   ['ILMN_1760320', 'ILMN_2115336', 'ILMN_2137312...  

[2294 rows x 3 columns]

In [2]:
genes_components_per_pathway = {} #nested dictionary where the 'outer dictionary' is the pathway names as keys and values are 
                                  #another dictionary with genes as keys and components as values

for pathway in reactome.index:
    genes = reactome.loc[pathway, "illumina"]
    print(genes)
    genes = literal_eval(genes)
    genes = list(filter(lambda a: a != 'NaN', genes))
    pathwaydata = dataset.loc[genes]
    if pathwaydata.index.empty == True:
        pass
    else:
        pathwaydata = pathwaydata.dropna(axis = 0, how = 'any') #has to be done so the lists match, this makes the dropna in my_pca function obsolete
        presentgenes = pathwaydata.index.values.tolist()
        if len(presentgenes) <= 1:
            pass
        else:
            res, components, explained_variance = my_pca(pathwaydata)
            print(res)
            pathwayname = reactome.loc[pathway, 'pathway_name']
            pca_per_pathway[pathwayname] = res

            components = components.tolist()[0]
            innerdict = {}
            for i in range(0, len(presentgenes)):
                component = components[i]
                gene = genes[i]
                if gene in real_gene_names.index:
                    real_name = real_gene_names.loc[gene, "symbol"]
                    innerdict[real_name] = component
                elif gene in gprofiler_names.index:
                    real_name = gprofiler_names.loc[gene, 'name']
                    innerdict[real_name] = component
                else:
                    innerdict[gene] = component
            sorted_innerdict = sorted(innerdict.items(), key = operator.itemgetter(1), reverse = True)
            genes_components_per_pathway[pathwayname] = [sorted_innerdict, explained_variance.flat[0]]

pca_per_pathway = pca_per_pathway.iloc[1:]

['ILMN_1683178', 'ILMN_1676955', 'ILMN_2181968', 'ILMN_1691364', 'ILMN_1746604', 'ILMN_1699651', 'ILMN_1696394', 'ILMN_1793384', 'ILMN_1663618', 'ILMN_1778236', 'ILMN_2156250']
                1
MB-0002 -0.464912
MB-0008  1.135677
MB-0010 -0.016406
MB-0035 -0.045984
MB-0036 -1.107911
...           ...
MB-7295 -0.097626
MB-7296 -0.616957
MB-7297 -0.546331
MB-7298  1.160626
MB-7299  0.110471

[1992 rows x 1 columns]
['ILMN_1738652', 'ILMN_1789830', 'ILMN_1789176', 'ILMN_2395389', 'ILMN_2259495', 'ILMN_1782538', 'ILMN_1808132', 'ILMN_1805990', 'ILMN_1791847', 'ILMN_1770940', 'ILMN_1682098', 'ILMN_1704196', 'ILMN_1673757', 'ILMN_1733421', 'ILMN_1808768', 'ILMN_1763540', 'ILMN_1736112', 'ILMN_2138801', 'ILMN_1778188', 'ILMN_1663454', 'ILMN_2321064', 'ILMN_1780189', 'ILMN_1759252', 'ILMN_2286800', 'ILMN_1748831', 'ILMN_2300186', 'ILMN_1806017', 'ILMN_1691165', 'ILMN_1720926', 'ILMN_1677032', 'ILMN_1733256', 'ILMN_1706677', 'ILMN_2109489', 'ILMN_2096759', 'ILMN_2387553', 'ILMN_1721659', 'ILMN

                 1
MB-0002   7.995568
MB-0008  -1.468536
MB-0010   1.688639
MB-0035  14.221326
MB-0036   5.790793
...            ...
MB-7295  -5.748507
MB-7296   1.617398
MB-7297  -2.774324
MB-7298  -3.616640
MB-7299 -12.366576

[1992 rows x 1 columns]
['ILMN_1738652', 'ILMN_2259495', 'ILMN_1805990', 'ILMN_1673757', 'ILMN_2138801', 'ILMN_1778188', 'ILMN_2321064', 'ILMN_1748831', 'ILMN_2300186', 'ILMN_1706677', 'ILMN_2109489', 'ILMN_2051469', 'ILMN_1844132', 'ILMN_1667260', 'ILMN_1810239', 'ILMN_1743347', 'NaN', 'ILMN_2192281', 'ILMN_2364574', 'ILMN_2402172', 'ILMN_1668996', 'ILMN_1807535', 'ILMN_1793671', 'ILMN_2325610', 'ILMN_1659463', 'ILMN_1690546', 'ILMN_1728512', 'ILMN_1718070', 'ILMN_1674385', 'ILMN_1762678', 'ILMN_1681497', 'ILMN_1779356', 'ILMN_2098446', 'ILMN_1748661', 'ILMN_1779706', 'ILMN_1717714', 'ILMN_2128293', 'ILMN_1766541', 'ILMN_2388155', 'ILMN_1801928', 'ILMN_1730332', 'ILMN_1694385', 'ILMN_1663618', 'ILMN_1710216', 'ILMN_1750145', 'ILMN_1654118', 'ILMN_1801119', 'Na

[1992 rows x 1 columns]
['ILMN_1738652', 'ILMN_2259495', 'ILMN_1810239', 'NaN', 'ILMN_2098446', 'ILMN_1766541', 'ILMN_1663618', 'ILMN_1654118', 'ILMN_1801119']
                1
MB-0002 -2.220955
MB-0008  0.153177
MB-0010  0.303371
MB-0035  2.075834
MB-0036 -1.113195
...           ...
MB-7295 -0.015287
MB-7296  1.339491
MB-7297 -0.446341
MB-7298 -0.697151
MB-7299 -1.007096

[1992 rows x 1 columns]
['ILMN_1805990', 'ILMN_2321064', 'ILMN_2402172', 'NaN', 'ILMN_2310589', 'ILMN_2310589']
                1
MB-0002 -1.448334
MB-0008  1.129965
MB-0010 -0.979819
MB-0035  0.656866
MB-0036 -0.558516
...           ...
MB-7295 -0.517899
MB-7296  0.790716
MB-7297  2.539919
MB-7298 -0.800759
MB-7299 -0.550131

[1992 rows x 1 columns]
['ILMN_1706677', 'ILMN_1844132', 'ILMN_1667260', 'ILMN_2192281', 'ILMN_1659463', 'ILMN_1718070', 'ILMN_1681497', 'ILMN_2128293', 'ILMN_1710216', 'NaN', 'ILMN_2310589', 'ILMN_2310589']
                1
MB-0002 -2.534688
MB-0008 -1.087412
MB-0010 -1.867067
MB-0035 -0.379

['ILMN_1711049', 'ILMN_2240923', 'ILMN_1702149', 'ILMN_2340815', 'ILMN_1691855', 'ILMN_1754076', 'ILMN_1814856', 'ILMN_2406106', 'ILMN_1769492', 'ILMN_2195482', 'ILMN_1685164', 'ILMN_1664047', 'ILMN_1814856']
                1
MB-0002  1.243149
MB-0008  1.507903
MB-0010  0.708913
MB-0035  1.243570
MB-0036  0.960869
...           ...
MB-7295 -0.972098
MB-7296  0.108119
MB-7297 -1.265419
MB-7298 -0.588577
MB-7299 -2.844840

[1992 rows x 1 columns]
['NaN', 'ILMN_1783837', 'ILMN_1707710', 'ILMN_1838187', 'ILMN_2305843', 'NaN', 'ILMN_1700759', 'ILMN_1789642', 'ILMN_1697512', 'ILMN_1663444', 'ILMN_1770629', 'ILMN_2171471', 'ILMN_1755369', 'ILMN_1760160', 'ILMN_1658917', 'ILMN_2182656', 'ILMN_2413084', 'ILMN_1785380', 'ILMN_1806293', 'NaN', 'ILMN_2372398', 'ILMN_1762410', 'ILMN_2188722', 'ILMN_1803748', 'ILMN_1812859', 'ILMN_1800164', 'ILMN_1798577', 'ILMN_1740555', 'ILMN_1651799', 'ILMN_1677439', 'ILMN_1728301', 'ILMN_1810657', 'ILMN_2391512', 'ILMN_1803318', 'ILMN_1663096', 'ILMN_1769810', 

                1
MB-0002  1.222823
MB-0008 -0.269884
MB-0010 -0.581865
MB-0035  2.606188
MB-0036  5.641198
...           ...
MB-7295 -4.184742
MB-7296 -2.484049
MB-7297 -3.091396
MB-7298 -3.170331
MB-7299 -5.184743

[1992 rows x 1 columns]
['ILMN_2382705', 'ILMN_1684850', 'NaN', 'ILMN_1767129', 'ILMN_1768758', 'ILMN_1681998', 'ILMN_1711049', 'ILMN_1783837', 'ILMN_1707710', 'ILMN_1686610', 'ILMN_2380938', 'ILMN_1715551', 'ILMN_1700657', 'ILMN_1802633', 'ILMN_1673769', 'ILMN_1810593', 'ILMN_1723626', 'ILMN_1809957', 'ILMN_1811579', 'ILMN_2409520', 'ILMN_2338809', 'ILMN_1779386', 'ILMN_2315208', 'ILMN_1696003', 'ILMN_2240923', 'ILMN_1838187', 'ILMN_2342762', 'ILMN_2366473', 'ILMN_1712348', 'ILMN_2305843', 'ILMN_1666445', 'ILMN_1702501', 'ILMN_1786195', 'ILMN_1807968', 'ILMN_1694810', 'ILMN_1680687', 'ILMN_1788663', 'ILMN_1702149', 'ILMN_1701958', 'ILMN_2215640', 'ILMN_1654422', 'ILMN_1810691', 'ILMN_1760320', 'NaN', 'ILMN_1805448', 'ILMN_1700759', 'ILMN_2154157', 'ILMN_1749996', 'ILMN_17

...

[1992 rows x 1 columns]
['ILMN_2397602', 'ILMN_2373515', 'ILMN_1668369', 'ILMN_1666910', 'ILMN_2352401', 'ILMN_2121408', 'ILMN_1767135', 'ILMN_1705396', 'ILMN_2382906', 'ILMN_1657248', 'ILMN_1728071', 'ILMN_1690733', 'ILMN_1717902', 'ILMN_1689057', 'ILMN_1696521', 'ILMN_1737252', 'ILMN_2337880', 'ILMN_1701967', 'ILMN_1804662', 'ILMN_1699798', 'ILMN_2081070', 'ILMN_1742521', 'ILMN_1653728', 'ILMN_1774945', 'ILMN_1775759', 'ILMN_1699798']
                1
MB-0002 -0.556674
MB-0008 -0.985385
MB-0010  0.292261
MB-0035  2.091285
MB-0036  0.348600
...           ...
MB-7295 -1.181473
MB-7296  0.389614
MB-7297 -0.321762
MB-7298 -0.786250
MB-7299 -1.151466

[1992 rows x 1 columns]
['ILMN_2373515', 'ILMN_1668369', 'ILMN_2352401', 'ILMN_1717902']
                1
MB-0002 -0.066761
MB-0008 -0.707658
MB-0010  0.981737
MB-0035  0.563119
MB-0036  0.056669
...           ...
MB-7295 -1.387295
MB-7296  1.204695
MB-7297  0.228649
MB-7298 -0.469699
MB-7299 -0.809017

[1992 rows x 1 columns]
['ILMN_23735

[1992 rows x 1 columns]
['ILMN_1766475']
['ILMN_1741422', 'ILMN_1755643', 'ILMN_1756501', 'NaN', 'ILMN_1765187', 'ILMN_2204545', 'ILMN_2147435', 'ILMN_1736828', 'ILMN_1721391', 'ILMN_1732555', 'ILMN_2380688', 'ILMN_1795845', 'ILMN_1766475', 'ILMN_1734176', 'ILMN_1758461', 'ILMN_1698508', 'ILMN_1731049', 'ILMN_1685824', 'ILMN_1692267', 'ILMN_1796106', 'ILMN_2342240', 'ILMN_1653358', 'ILMN_1697301', 'ILMN_1752728', 'ILMN_2117736', 'ILMN_1815148', 'ILMN_2117736', 'ILMN_1796106', 'NaN']
                1
MB-0002 -0.046703
MB-0008 -0.982091
MB-0010 -1.392189
MB-0035  0.356305
MB-0036 -0.019407
...           ...
MB-7295 -2.516768
MB-7296  0.538455
MB-7297 -1.908858
MB-7298  0.492214
MB-7299 -2.536128

[1992 rows x 1 columns]
['ILMN_1755643', 'ILMN_1756501', 'NaN', 'ILMN_2204545', 'ILMN_1721391', 'ILMN_1732555', 'ILMN_2380688', 'ILMN_1758461', 'ILMN_1698508', 'ILMN_1731049', 'ILMN_1685824', 'ILMN_1692267', 'ILMN_1796106', 'ILMN_1697301', 'ILMN_2117736', 'ILMN_2117736', 'ILMN_1796106', 'NaN']


[1992 rows x 1 columns]
['ILMN_1704537', 'ILMN_1741613', 'ILMN_1665065', 'ILMN_1692938', 'ILMN_1776105', 'NaN', 'ILMN_1753515', 'ILMN_2111932', 'ILMN_1704512']
                1
MB-0002 -0.670302
MB-0008  0.712861
MB-0010  0.292843
MB-0035  0.033283
MB-0036 -1.593180
...           ...
MB-7295 -0.915469
MB-7296 -0.362503
MB-7297 -1.005777
MB-7298 -1.005479
MB-7299  0.186675

[1992 rows x 1 columns]
['ILMN_1715551', 'ILMN_1802633', 'ILMN_1696003', 'ILMN_1810691', 'ILMN_1760320', 'ILMN_1801408', 'ILMN_2115336', 'ILMN_1676870', 'ILMN_2413964', 'ILMN_1775762', 'ILMN_2137312', 'ILMN_1655935', 'ILMN_1780334', 'ILMN_2091100', 'ILMN_1742044', 'ILMN_2148944', 'ILMN_1779370', 'ILMN_1660718', 'ILMN_1676893', 'ILMN_1746027', 'NaN', 'ILMN_1798046', 'ILMN_1760431', 'ILMN_1659678', 'ILMN_1736045', 'ILMN_1754440', 'ILMN_1753975', 'ILMN_1805376', 'ILMN_2396903', 'ILMN_1654287', 'ILMN_1806147', 'ILMN_2177928', 'ILMN_1684945', 'ILMN_2159730', 'ILMN_1742073', 'ILMN_1660608', 'ILMN_1671237', 'ILMN_1693269',

                 1
MB-0002  10.501030
MB-0008  -4.968356
MB-0010   2.602106
MB-0035  11.536756
MB-0036   2.737150
...            ...
MB-7295  -0.410081
MB-7296   0.600571
MB-7297  -6.728891
MB-7298  -5.495022
MB-7299 -11.564783

[1992 rows x 1 columns]
['ILMN_1773865', 'ILMN_2129309', 'ILMN_1742450', 'ILMN_2126832', 'NaN', 'ILMN_1762861', 'ILMN_2399896', 'ILMN_1745469', 'ILMN_1656386', 'ILMN_2394296', 'NaN', 'ILMN_2336220', 'ILMN_2123312', 'ILMN_2148459', 'ILMN_1669753', 'ILMN_1751079', 'ILMN_1676600', 'ILMN_1736256', 'ILMN_1812403', 'ILMN_1759250', 'ILMN_2150787', 'ILMN_1765258', 'ILMN_1656670', 'ILMN_1762861', 'ILMN_1742450', 'ILMN_1777565', 'ILMN_1742450', 'ILMN_1751079', 'ILMN_1759250', 'ILMN_1778401', 'ILMN_1765258', 'ILMN_1671054', 'ILMN_2165753', 'ILMN_1656670', 'ILMN_1762861', 'ILMN_1777565', 'ILMN_1778401', 'ILMN_2165753', 'ILMN_1751079', 'ILMN_1778401', 'ILMN_1765258', 'NaN', 'ILMN_1759250', 'ILMN_1751079', 'ILMN_1751079', 'NaN', 'ILMN_1759250', 'ILMN_1778401', 'ILMN_1765258'

[1992 rows x 1 columns]
['ILMN_1760320', 'ILMN_2115336', 'ILMN_2137312', 'ILMN_1780334', 'ILMN_2091100', 'ILMN_1660718', 'ILMN_1736045', 'ILMN_1805376', 'ILMN_2396903', 'ILMN_1806147', 'ILMN_2177928', 'ILMN_1684945', 'ILMN_1671237', 'ILMN_1693269', 'ILMN_1800179', 'ILMN_1804357', 'ILMN_1658928', 'ILMN_1673380', 'ILMN_1701854', 'ILMN_1728107', 'ILMN_1808272', 'ILMN_1794200', 'ILMN_1807925', 'ILMN_1678841', 'ILMN_2395375', 'ILMN_2395375', 'ILMN_2395375', 'ILMN_1678841', 'ILMN_2395375', 'ILMN_2395375', 'ILMN_1652003', 'ILMN_1804357']
                1
MB-0002 -1.718518
MB-0008  0.911406
MB-0010 -1.831641
MB-0035  2.369227
MB-0036 -1.141990
...           ...
MB-7295 -3.079482
MB-7296 -0.717144
MB-7297 -4.411178
MB-7298 -2.664393
MB-7299 -1.081328

[1992 rows x 1 columns]


In [6]:
mutation_df.shape

(2369, 173)

In [5]:
mutation_df = pd.read_csv("../data/mutations_per_patients.csv", sep=",", index_col = 0)

In [7]:
full_df = pd.concat([pca_per_pathway, mutation_df.reindex(pca_per_pathway.index)], axis= 1)
full_df
mutations = full_df.iloc[:,-173:]

In [8]:
from scipy.stats import ttest_ind, mannwhitneyu
import qvalue as qv

clusterframes = {}



for column in mutations:
    #mutated_gene = mutations[column]
    grouped_by_cluster = full_df.groupby(column)
    for group in grouped_by_cluster:
        df_cluster = pd.DataFrame(index=full_df.iloc[:,:-173].columns)
        groupname = group[0]
        df = group[1].iloc[:,:-173]
        group2_df = full_df[full_df[column] != groupname].iloc[:,:-173]
        pvaluelist = []
        group1_mean_list = []
        group2_mean_list = []
        for pathway in df:
            group = df[pathway]
            group2 = group2_df[pathway]
            test = mannwhitneyu(group, group2)
            pvaluelist.append(test[1])
            group_mean = group.mean()
            group1_mean_list.append(group_mean)
            group2_mean = group2.mean()
            group2_mean_list.append(group2_mean) 
        
    
    df_cluster[f'{groupname}'] = group1_mean_list
    df_cluster['Other samples'] = group2_mean_list
    df_cluster['Fold Change'] = np.log2(abs(df_cluster[f'{groupname}'])) - np.log2(abs(df_cluster['Other samples']))
    
    
    df_cluster['p-values'] = pvaluelist
    qv.qvalues(df_cluster, 'p-values', f'{groupname} qvalues')
    df_cluster['p-values'] = -np.log10(df_cluster['p-values'])
    df_cluster[f'{groupname} qvalues'] = -np.log10(df_cluster[f'{groupname} qvalues'])
    print(column)
    clusterframes[column] = [df_cluster, mutations[column].value_counts()]
    #clusterframes[column] = df_cluster

        
clusterframes

TP53
MLLT4
NF2
SF3B1
NT5E
EGFR
PRKCQ
AHNAK
CLK3
ERBB2
MUC16
EP300
HIST1H2BC
UBR5
USP28
AHNAK2
BIRC6
PIK3CA
MAP3K13
COL12A1
FOXO3
SYNE1
NRG3
DNAH2
NF1
SETDB1
COL6A3
ATR
KMT2C
GPR124
ARID2
ERBB3
SIK1
TAF1
PTEN
AKT1
FANCA
MLL2
BRCA1
DNAH11
AKAP9
STAB2
HERC2
CACNA2D3
RYR2
PALLD
ARID1A
LAMB3
SBNO1
NCOA3
STK11
MAP3K1
PIK3R1
UTRN
TG
HRAS
FANCD2
SHANK2
NPNT
USH2A
PBRM1
CDH1
MYH9
MAP2K4
NCOR1
PTPRD
TBX3
CBFB
CTCF
RUNX1
COL22A1
NCOR2
DNAH5
GATA3
AFF2
ALK
MAP3K10
BRCA2
KDM3A
FAM20C
MAGEA8
L1CAM
PRKCZ
GPS2
USP9X
PTPN22
PDE4DIP
GPR32
LARGE
THSD7A
SIAH1
LAMA2
HDAC9
ARID1B
FLT3
PRKCE
AGTR2
PTPRM
CTNNA3
CTNNA1
ROS1
RPGR
PRR16
ASXL1
SETD1A
AKT2
MBL2
GH1
SGCD
KDM6A
BRAF
CASP8
SETD2
SMARCC1
NR3C1
DCAF4L2
MYO1A
CHEK2
KRAS
LIFR
DTWD2
NOTCH1
GLDC
THADA
PRPS2
FRMD3
MYO3A
ACVRL1
SMARCC2
TTYH1
FOXO1
OR6A2
APC
RB1
SMARCB1
CLRN2
MTAP
FBXW7
ARID5B
PRKACG
PRKG1
BCAS3
ZFP36L1
TBL1XR1
BAP1
SPACA1
JAK1
CHD1
FOXP1
ASXL2
AGMO
LIPI
SMAD4
BRIP1
ERBB4
MEN1
CDKN1B
CDKN2A
RASGEF1B
NDFIP1
PPP2R2A
SMAD2
SIK2
NEK1
SMARCD1
NR2F

{'TP53': [                                                          WT  Other samples  \
  Transcriptional Regulation by MECP2                -1.069762       1.641391   
  G1 Phase                                           -1.180159       1.810777   
  Cyclin D associated events in G1                   -1.180159       1.810777   
  DAG and IP3 signaling                               0.879302      -1.349156   
  Serine biosynthesis                                -0.629849       0.966409   
  SLC-mediated transmembrane transport               -1.824355       2.799202   
  Activation of AMPK downstream of NMDARs             0.914358      -1.402947   
  Metabolism of nucleotides                          -1.360173       2.086983   
  Activation of NMDA receptors and postsynaptic e...  1.127821      -1.730474   
  Post NMDA receptor activation events                1.102714      -1.691950   
  Ubiquinol biosynthesis                             -0.583281       0.894958   
  Nucleotide salvage

In [9]:
high_q = []
for mut in clusterframes:
    i = clusterframes[mut]
    if i[0].iloc[:1,4:].values[0][0] >= 10:
        print(mut)
        print(i[0].iloc[:1,4:].values[0][0]) #this is the q-value of the pathway with the highest q-value -_-
        high_q.append(mut)

TP53
140.57400760110372
PIK3CA
42.614925617620074
MAP3K1
11.341251936099614
CDH1
16.544582197862848
CBFB
13.248201260330292
GATA3
14.392987649195767


In [10]:
high_q_df = pd.DataFrame(index = clusterframes['TP53'][0].index)
for i in high_q:
    q_values = clusterframes[i][0].iloc[:,4:]
    high_q_df[i] = q_values

    
high_q_df.sort_values(by='CDH1', ascending = False)
high_q_df.to_csv('../exp/mutations_with_high_q.csv')
    

In [13]:
ER_Pos_driver_genes = ['PIK3CA', 'TP53', "GATA3", "CDH1", "MAP3K1",
                       "KMT2C", "AKT1", "CBFB", "RB1"]
BRCA_genes = ['BRCA1', "BRCA2"]

clusterframes['BRCA2']

[                                                          WT  Other samples  \
 Spry regulation of FGF signaling                    0.058107      -0.630874   
 Defective CYP11A1 causes Adrenal insufficiency,... -0.047314       0.513698   
 Sphingolipid de novo biosynthesis                   0.096352      -1.046112   
 Negative regulation of FGFR2 signaling              0.056177      -0.609918   
 Nuclear Events (kinase and transcription factor...  0.060463      -0.656457   
 ERK/MAPK targets                                    0.057848      -0.628060   
 ERKs are inactivated                                0.048255      -0.523906   
 Negative regulation of FGFR4 signaling              0.057284      -0.621943   
 MAPK targets/ Nuclear events mediated by MAP ki...  0.067023      -0.727674   
 Regulation of TP53 Activity                         0.142852      -1.550961   
 TP53 Regulates Transcription of Death Receptors...  0.044354      -0.481559   
 Processing of Intronless Pre-mRNAs     

In [14]:
high_q_df = pd.DataFrame(index = clusterframes['TP53'][0].index)
for i in ER_Pos_driver_genes:
    q_values = clusterframes[i][0].iloc[:,4:]
    high_q_df[i] = q_values
    
for i in BRCA_genes:
    q_values = clusterframes[i][0].iloc[:,4:]
    high_q_df[i] = q_values

In [15]:
high_q_df.to_csv('../exp/mutations_with_high_q.csv')